# Project INS RNA-seq data

Project INS RNA-seq data to Multiplier model and study differential LVs.

# Load libraries/modules

In [1]:
library(biomaRt)
library(here)
library(biomaRt)
library(DESeq2)
library(tidyverse)
library(rtracklayer)
library(dplyr)
library(GenomicRanges)
library(ggpubr)
library(cowplot)
# load plier utils
source(here::here('scripts/plier_util.R'))

here() starts at /home/msubirana/Documents/pivlab/plier_recount3

Loading required package: S4Vectors

Loading required package: stats4

Loading required package: BiocGenerics


Attaching package: ‘BiocGenerics’


The following objects are masked from ‘package:stats’:

    IQR, mad, sd, var, xtabs


The following objects are masked from ‘package:base’:

    anyDuplicated, aperm, append, as.data.frame, basename, cbind,
    colnames, dirname, do.call, duplicated, eval, evalq, Filter, Find,
    get, grep, grepl, intersect, is.unsorted, lapply, Map, mapply,
    match, mget, order, paste, pmax, pmax.int, pmin, pmin.int,
    Position, rank, rbind, Reduce, rownames, sapply, setdiff, sort,
    table, tapply, union, unique, unsplit, which.max, which.min



Attaching package: ‘S4Vectors’


The following object is masked from ‘package:utils’:

    findMatches


The following objects are masked from ‘package:base’:

    expand.grid, I, unname


Loading required package: IRanges

Loading required p

# Load data

In [27]:
# define output nb
output_nb_path = here('output/nbs/project_ins_rnaseq_data')
dir.create(output_nb_path, showWarnings = FALSE)

counts_matrix=here::here('data/ins/RNA_INS_RAW.txt')

# multiplier model
multiplier_z = readRDS(here('data/multiplier/multiplier_model_z.rds'))
multiplier_summary = readRDS(here('data/multiplier/multiplier_model_summary.rds'))
multiplier_b = readRDS(here('data/multiplier/multiplier_model_b.rds'))
multiplier_metadata = readRDS(here('data/multiplier/multiplier_model_metadata.rds'))
multiplier_U = readRDS(here('data/multiplier/multiplier_model_u.rds'))

# TPM Normalization Process

TPM (Transcripts Per Kilobase Million) is a method for normalizing RNA sequencing data. It helps in comparing gene expression levels across different samples. The steps to compute TPM are as follows:

1. **Load the Data**: Import your gene count data into R.
2. **Calculate Gene Lengths**: Obtain or calculate the length of each gene in kilobases. This data is necessary for the normalization process.
3. **Compute Scaled Reads**: Divide each gene's read count by its length in kilobases to account for gene length and get scaled reads.
4. **Sum Scaled Reads**: Calculate the sum of all the scaled reads across all genes in a sample. This sum will be used to normalize the read counts so that they are comparable across samples.
5. **Calculate TPM**: Normalize each gene's scaled reads by the sum of scaled reads across all genes and multiply by 1,000,000. This final step adjusts for the total amount of transcript in each sample, allowing for comparisons across samples.


# INS RNA-seq analysis

def

In [10]:
gene_counts_ins <- read.table(counts_matrix, header = TRUE, sep = "\t", check.names = FALSE)
head(gene_counts_ins)

NET101 NET102 NET103 NET106 NET107 NET109 NET10 NET11 NET14
ENSG00000000419 1578   717    848    1237    945   1823    915  2264  1408 
ENSG00000000457  961   428    475     468    796    881    724  1194  1684 
ENSG00000000460  194   157    195     323    332    292    129   304   304 
ENSG00000000938  362    78    110     158    319    135    222   181   229 
ENSG00000000971 5078   235    661     733    359   1267    657  2727  1521 
ENSG00000001036 8127   879    691     556   1548   1376   8614  4046  4226 
                NET16 ⋯ HI01 HI02 HI03 HI04 HI05 BETA05 BETA06 HI06 HI07 HI09
ENSG00000000419  247  ⋯ 1526 2162 1661 2078 2283 2326   1297   488   454  808
ENSG00000000457  133  ⋯ 1142 1625 1312 1478 2117  966    297   341   808  593
ENSG00000000460   34  ⋯  277  302  273  348  396  484     98   167   172  141
ENSG00000000938   97  ⋯   48   65   20   45   35   15      9     3     5    7
ENSG00000000971   63  ⋯ 6050 1893 1075 2924 6694   98     22   127   255  340
ENSG00000001036 2804  ⋯ 4795 6910 5435 5500 7456 3051   1353   711  1617 1825

In [11]:
# Initialize the Ensembl Mart
ensembl <- useMart("ensembl", dataset = "hsapiens_gene_ensembl")

# Your Geneid values
gene_ids <- rownames(gene_counts_ins)

# Query Ensembl for gene symbols
gene_info <- getBM(attributes = c("ensembl_gene_id", "external_gene_name"), 
                   filters = "ensembl_gene_id", 
                   values = gene_ids, 
                   mart = ensembl)

# Rename columns for merging
colnames(gene_info) <- c("Geneid", "GeneSymbol")

# Merge the gene_info with your gene_counts_ins data frame
gene_counts_ins <- merge(gene_info, gene_counts_ins, by.x = "Geneid", by.y = "row.names")

# Set the row names to Geneid
rownames(gene_counts_ins) <- gene_counts_ins$Geneid
rownames(gene_counts_ins) <- 1:nrow(gene_counts_ins)
# View the modified data frame
head(gene_counts_ins)

Geneid          GeneSymbol NET101 NET102 NET103 NET106 NET107 NET109 NET10
1 ENSG00000000419 DPM1       1578   717    848    1237    945   1823    915 
2 ENSG00000000457 SCYL3       961   428    475     468    796    881    724 
3 ENSG00000000460 FIRRM       194   157    195     323    332    292    129 
4 ENSG00000000938 FGR         362    78    110     158    319    135    222 
5 ENSG00000000971 CFH        5078   235    661     733    359   1267    657 
6 ENSG00000001036 FUCA2      8127   879    691     556   1548   1376   8614 
  NET11 ⋯ HI01 HI02 HI03 HI04 HI05 BETA05 BETA06 HI06 HI07 HI09
1 2264  ⋯ 1526 2162 1661 2078 2283 2326   1297   488   454  808
2 1194  ⋯ 1142 1625 1312 1478 2117  966    297   341   808  593
3  304  ⋯  277  302  273  348  396  484     98   167   172  141
4  181  ⋯   48   65   20   45   35   15      9     3     5    7
5 2727  ⋯ 6050 1893 1075 2924 6694   98     22   127   255  340
6 4046  ⋯ 4795 6910 5435 5500 7456 3051   1353   711  1617 1825

In [12]:
gtf_path <- here::here('data/GCF_000001405.38_GRCh38.p12_genomic.gtf')
tpm_gene_counts_ins=tpm_normalization(gene_counts_ins, gtf_path)
head(tpm_gene_counts_ins)

Joining with `by = join_by(GeneSymbol)`


NET101    NET102    NET103    NET106    NET107    NET109    NET10    
DPM1  10.349157 20.567900 38.076160 33.839553 19.083286 22.337757  6.640231
SCYL3  3.627532  7.066500 12.275543  7.368695  9.251757  6.213247  3.024061
FGR    2.418723  2.279528  5.031871  4.403434  6.562836  1.685257  1.641325
CFH    8.257107  1.671383  7.358614  4.971600  1.797434  3.849167  1.182129
FUCA2 74.025701 35.019823 43.091302 21.124381 43.415676 23.416695 86.820291
GCLC   6.322156 12.879938 22.677723 12.377819 11.481545  8.377154  4.676981
      NET11     NET14     NET16      ⋯ HI01       HI02       HI03      
DPM1  24.360613 11.528386  3.0722273 ⋯  9.6208177 11.0603931  9.3858385
SCYL3  7.394451  7.935929  0.9521335 ⋯  4.1439391  4.7847368  4.2670437
FGR    1.984129  1.910209  1.2291578 ⋯  0.3083033  0.3387722  0.1151365
CFH    7.275020  3.087680  0.1942827 ⋯  9.4569278  2.4010585  1.5060839
FUCA2 60.463312 48.056223 48.4382757 ⋯ 41.9855973 49.0961225 42.6537547
GCLC   5.578564 23.934424  1.9685274 ⋯ 11.9610613 11.3097873  9.4505390
      HI04       HI05       BETA05      BETA06      HI06       HI07       
DPM1  11.8444808 13.7531293 13.24217613 21.87148790 18.8907450  6.80621057
SCYL3  4.8488052  7.3401729  3.16531248  2.88260156  7.5975481  6.97189285
FGR    0.2613139  0.2148044  0.08700024  0.15461812  0.1183123  0.07636583
CFH    4.1322359  9.9981252  0.13832892  0.09198103  1.2189060  0.94782237
FUCA2 43.5399023 62.3814964 24.12382290 31.68767854 38.2254969 33.66772896
GCLC  15.0783913 16.4381404 27.48254017 26.12791284  9.9484038 11.17156051
      HI09      
DPM1  17.0561343
SCYL3  7.2046644
FGR    0.1505382
CFH    1.7794484
FUCA2 53.5040169
GCLC  13.0281877

# Multiplier projection

In [13]:
multiplier_model = list('Z'=multiplier_z, 'L2'= multiplier_metadata$L2, 'B'=multiplier_b, 'U'=multiplier_U)

In [14]:
result_GetOrderedRowNormEM <- GetOrderedRowNormEM(tpm_gene_counts_ins, multiplier_model)
ordered_tpm_gene_counts_ins = result_GetOrderedRowNormEM$exprs.norm.filtered
ordered_multiplier_model = result_GetOrderedRowNormEM$plier.model

head(ordered_tpm_gene_counts_ins)
head(ordered_multiplier_model$Z)

Loading required package: PLIER

Loading required package: RColorBrewer

Loading required package: gplots


Attaching package: ‘gplots’


The following object is masked from ‘package:rtracklayer’:

    space


The following object is masked from ‘package:IRanges’:

    space


The following object is masked from ‘package:S4Vectors’:

    space


The following object is masked from ‘package:stats’:

    lowess


Loading required package: pheatmap

Loading required package: glmnet

Loading required package: Matrix


Attaching package: ‘Matrix’


The following objects are masked from ‘package:tidyr’:

    expand, pack, unpack


The following object is masked from ‘package:S4Vectors’:

    expand


Loaded glmnet 4.1-8

Loading required package: knitr

Loading required package: rsvd

Loading required package: qvalue



NET101     NET102      NET103    NET106     NET107      NET109    
DPM1    -0.6409373  0.12552006 1.4387281  1.1209611  0.01416645  0.2582682
FGR      0.8977851  0.80048592 2.7244150  2.2851284  3.79458250  0.3850817
CFH      1.3577481 -0.43904544 1.1126106  0.4613579 -0.40465459  0.1551228
GCLC    -0.9715021 -0.05706912 1.3091577 -0.1270857 -0.25206434 -0.6849482
NFYA    -1.0243933  0.58932874 0.2044962  0.9910376  1.21766405 -0.8945847
CYP51A1 -1.2073189  0.35954365 0.3699140 -0.2704209 -0.68061722 -0.8891094
        NET10      NET11      NET14       NET16      ⋯ HI01       HI02       
DPM1    -0.9191256  0.4099927 -0.55248920 -1.1867439 ⋯ -0.6955665 -0.58759106
FGR      0.3543725  0.5939975  0.54232636  0.0662614 ⋯ -0.5774297 -0.55613152
CFH     -0.5725294  1.0898035 -0.05263477 -0.8420449 ⋯  1.6850969 -0.23996688
GCLC    -1.2009092 -1.0751902  1.48439517 -1.5785825 ⋯ -0.1851995 -0.27601468
NFYA    -0.8540972 -0.4276035 -0.88425530 -1.6773714 ⋯  0.5623366  0.90592969
CYP51A1 -0.2662395  0.7894828 -0.26627478 -1.4623365 ⋯ -0.8523937  0.09022678
        HI03         HI04       HI05       BETA05     BETA06     HI06         
DPM1    -0.713191120 -0.5287805 -0.3856222 -0.4239463  0.2232957 -0.0002750607
FGR     -0.712456240 -0.6102760 -0.6427869 -0.7321239 -0.6848580 -0.7102362693
CFH     -0.484144191  0.2323530  1.8327527 -0.8573109 -0.8699561 -0.5624953621
GCLC    -0.535272745  0.2494886  0.4390953  1.9791530  1.7902605 -0.4658492729
NFYA     0.002701273  0.4202043  1.3100700 -0.7193276 -0.2964648  1.3676120768
CYP51A1 -0.176026792 -0.3551017 -0.3191862 -0.3983455 -1.0722340 -0.5092284527
        HI07       HI09       
DPM1    -0.9066763 -0.13788015
FGR     -0.7395575 -0.68770989
CFH     -0.6364555 -0.40956171
GCLC    -0.2952894 -0.03639678
NFYA    -0.2269073  0.52897233
CYP51A1 -1.0246355 -0.31377384

[,1]       [,2]     [,3]       [,4]       [,5]        [,6]       
DPM1    0.00000000 0.000000 0.00000000 0.00000000 0.000000000 0.000000000
FGR     0.00000000 2.792407 0.00000000 0.00000000 0.000000000 0.007556259
CFH     0.09900812 0.000000 0.03310266 0.00000000 0.004552824 0.000000000
GCLC    0.00000000 0.000000 0.00000000 0.02639352 0.000000000 0.006502586
NFYA    0.07494908 0.000000 0.01228377 0.00000000 0.064057583 0.063490791
CYP51A1 0.00000000 0.000000 0.00000000 0.01935075 0.000000000 0.000000000
        [,7]        [,8]       [,9]       [,10]     [,11] [,12]     
DPM1    0.000000000 0.00000000 0.00000000 0.0000000 ⋯     0.08369499
FGR     1.427774876 0.00000000 0.05398429 0.0000000 ⋯     0.03084241
CFH     0.000000000 0.00000000 0.00000000 0.0000000 ⋯     0.00000000
GCLC    0.000000000 0.08185016 0.01321533 0.0000000 ⋯     0.00000000
NFYA    0.000000000 0.00000000 0.02041878 0.0282739 ⋯     0.00000000
CYP51A1 0.006564527 0.04239032 0.00000000 0.0000000 ⋯     0.00000000
        [,13]       [,14]      [,15]      [,16]       [,17]       [,18]     
DPM1    0.000000000 0.00000000 0.00000000 0.051272282 0.000000000 0.11906144
FGR     0.000000000 0.00000000 0.00000000 0.000000000 0.003921367 0.29229554
CFH     0.004358553 0.31948602 0.00000000 0.000000000 0.000000000 0.17165840
GCLC    0.000802744 0.00000000 0.00000000 0.004574412 0.024722275 0.03324841
NFYA    0.000000000 0.00000000 0.00000000 0.000000000 0.000000000 0.33060020
CYP51A1 0.255284314 0.06569657 0.04061676 0.000000000 0.071268524 0.00000000
        [,19]      [,20]    [,21]     
DPM1    0.00000000 0.000000 0.00000000
FGR     0.22627083 0.000000 0.00000000
CFH     0.00000000 0.000000 0.00000000
GCLC    0.07502169 0.000000 0.02796574
NFYA    0.46354184 0.000000 0.47592245
CYP51A1 0.00000000 1.335467 0.00000000

In [15]:
projection_ins <-  GetNewDataB(ordered_tpm_gene_counts_ins, ordered_multiplier_model)
head(projection_ins)

NET101      NET102      
1,REACTOME_MRNA_SPLICING                          0.15162940  0.121978756
2,SVM Monocytes                                   0.10072394  0.100415629
3,REACTOME_TRANSMISSION_ACROSS_CHEMICAL_SYNAPSES  0.21959047 -0.014146302
4,REACTOME_NEURONAL_SYSTEM                       -0.15302464 -0.002903181
LV 5                                             -0.02042750  0.026692836
LV 6                                              0.05410557  0.030783162
                                                 NET103      NET106      
1,REACTOME_MRNA_SPLICING                         -0.09359738  0.033702880
2,SVM Monocytes                                   0.23025597  0.180023518
3,REACTOME_TRANSMISSION_ACROSS_CHEMICAL_SYNAPSES -0.06369650  0.023441284
4,REACTOME_NEURONAL_SYSTEM                        0.31476651  0.049945287
LV 5                                              0.02595536  0.002952028
LV 6                                             -0.11400919 -0.056200313
                                                 NET107       NET109      
1,REACTOME_MRNA_SPLICING                          0.069508227  0.056409787
2,SVM Monocytes                                   0.025626518  0.144944762
3,REACTOME_TRANSMISSION_ACROSS_CHEMICAL_SYNAPSES  0.043356751 -0.023376263
4,REACTOME_NEURONAL_SYSTEM                       -0.025674547  0.002666081
LV 5                                             -0.002756633 -0.006190541
LV 6                                             -0.017175742 -0.031348460
                                                 NET10        NET11       
1,REACTOME_MRNA_SPLICING                          0.014005986  0.017298638
2,SVM Monocytes                                  -0.009958921  0.028446007
3,REACTOME_TRANSMISSION_ACROSS_CHEMICAL_SYNAPSES -0.054367449 -0.018848645
4,REACTOME_NEURONAL_SYSTEM                        0.071756188  0.187046668
LV 5                                             -0.044443695 -0.005783107
LV 6                                             -0.025643835  0.045523912
                                                 NET14       NET16         ⋯
1,REACTOME_MRNA_SPLICING                          0.15796600  0.0355323344 ⋯
2,SVM Monocytes                                   0.05153149  0.0574855302 ⋯
3,REACTOME_TRANSMISSION_ACROSS_CHEMICAL_SYNAPSES -0.02373190 -0.0278611742 ⋯
4,REACTOME_NEURONAL_SYSTEM                        0.02674699 -0.0174174201 ⋯
LV 5                                             -0.04353592 -0.0253902441 ⋯
LV 6                                              0.05047405 -0.0003731398 ⋯
                                                 HI01        HI02        
1,REACTOME_MRNA_SPLICING                          0.11530575  0.011129325
2,SVM Monocytes                                  -0.04841758 -0.067179045
3,REACTOME_TRANSMISSION_ACROSS_CHEMICAL_SYNAPSES -0.06480191 -0.006251083
4,REACTOME_NEURONAL_SYSTEM                       -0.11415594 -0.059160365
LV 5                                              0.03824690  0.023081742
LV 6                                              0.02844394  0.005588511
                                                 HI03         HI04        
1,REACTOME_MRNA_SPLICING                          0.020094170  0.054363544
2,SVM Monocytes                                  -0.058305376 -0.065090006
3,REACTOME_TRANSMISSION_ACROSS_CHEMICAL_SYNAPSES  0.049812510 -0.016391908
4,REACTOME_NEURONAL_SYSTEM                       -0.014451994 -0.058538979
LV 5                                             -0.012730584  0.018917553
LV 6                                             -0.005151429  0.007095962
                                                 HI05        BETA05      
1,REACTOME_MRNA_SPLICING                          0.05293075 -0.004502572
2,SVM Monocytes                                  -0.04955236 -0.044449786
3,REACTOME_TRANSMISSION_ACROSS_CHEMICAL_SYNAPSES -0.05252180  0.022019612
4,REACTOME_NEURONAL_SYSTEM                       -0.10731736 -0.005307093
LV 5       

In [76]:
df_projection_ins <- data.frame(projection_ins) %>%
  dplyr::mutate(LV = rownames(projection_ins)) %>%
  dplyr::select(LV, everything()) %>%
  `rownames<-`(1:nrow(projection_ins))


df_projection_ins$LV <- gsub('LV ', '', lapply(df_projection_ins$LV, function(x) unlist(strsplit(x, ','))[1]))
                       
head(df_projection_ins)

LV NET101      NET102       NET103      NET106       NET107      
1 1   0.15162940  0.121978756 -0.09359738  0.033702880  0.069508227
2 2   0.10072394  0.100415629  0.23025597  0.180023518  0.025626518
3 3   0.21959047 -0.014146302 -0.06369650  0.023441284  0.043356751
4 4  -0.15302464 -0.002903181  0.31476651  0.049945287 -0.025674547
5 5  -0.02042750  0.026692836  0.02595536  0.002952028 -0.002756633
6 6   0.05410557  0.030783162 -0.11400919 -0.056200313 -0.017175742
  NET109       NET10        NET11        NET14       ⋯ HI01        HI02        
1  0.056409787  0.014005986  0.017298638  0.15796600 ⋯  0.11530575  0.011129325
2  0.144944762 -0.009958921  0.028446007  0.05153149 ⋯ -0.04841758 -0.067179045
3 -0.023376263 -0.054367449 -0.018848645 -0.02373190 ⋯ -0.06480191 -0.006251083
4  0.002666081  0.071756188  0.187046668  0.02674699 ⋯ -0.11415594 -0.059160365
5 -0.006190541 -0.044443695 -0.005783107 -0.04353592 ⋯  0.03824690  0.023081742
6 -0.031348460 -0.025643835  0.045523912  0.05047405 ⋯  0.02844394  0.005588511
  HI03         HI04         HI05        BETA05       BETA06       HI06        
1  0.020094170  0.054363544  0.05293075 -0.004502572  0.002129012  0.151185849
2 -0.058305376 -0.065090006 -0.04955236 -0.044449786 -0.041177860  0.002581641
3  0.049812510 -0.016391908 -0.05252180  0.022019612  0.049472029  0.130966831
4 -0.014451994 -0.058538979 -0.10731736 -0.005307093 -0.021983590 -0.065830886
5 -0.012730584  0.018917553  0.07944170 -0.007901083  0.002868553  0.091037769
6 -0.005151429  0.007095962  0.01617550  0.016003255 -0.005230975  0.054324432
  HI07        HI09       
1  0.07821100  0.02405936
2 -0.03689034 -0.05313807
3  0.16052910  0.04748784
4 -0.17421378 -0.02482919
5  0.02819207  0.03626634
6  0.02946865  0.04066338

In [77]:
lv_data_long <- df_projection_ins %>%
  pivot_longer(cols = -LV, names_to = "Sample", values_to = "Value") %>%
  mutate(Group = case_when(
    str_detect(Sample, "^NET") ~ "INS",
    str_detect(Sample, "^BETA") ~ "BETA",
    str_detect(Sample, "^HI") ~ "HI",
    TRUE ~ "Other"
  ))

head(lv_data_long)

LV Sample Value       Group
1 1  NET101  0.15162940 INS  
2 1  NET102  0.12197876 INS  
3 1  NET103 -0.09359738 INS  
4 1  NET106  0.03370288 INS  
5 1  NET107  0.06950823 INS  
6 1  NET109  0.05640979 INS

In [84]:
# Function to perform Kruskal-Wallis test for each LV
kruskal_test_results <- lv_data_long %>%
  group_by(LV) %>%
  summarise(p_value = kruskal.test(Value ~ Group)$p.value)

# Multiple Testing Correction (FDR)
kruskal_test_results <- kruskal_test_results %>%
    mutate(p_adjusted = p.adjust(p_value, method = "fdr")) %>% 
    arrange(p_adjusted)

kruskal_test_results$p_value <-  NULL

In [85]:
head(kruskal_test_results)

LV  p_adjusted  
1 22  9.052299e-06
2 26  9.052299e-06
3 804 9.052299e-06
4 821 1.274292e-05
5 874 1.274292e-05
6 2   2.584017e-05

In [86]:
colnames(multiplier_summary)[2] <- 'LV'

In [87]:
head(multiplier_summary)

pathway                                 LV AUC       p-value     
1 KEGG_LYSINE_DEGRADATION                 1  0.3880591 8.660782e-01
2 REACTOME_MRNA_SPLICING                  1  0.7330575 4.772691e-05
3 MIPS_NOP56P_ASSOCIATED_PRE_RRNA_COMPLEX 1  0.6805546 1.628217e-03
4 KEGG_DNA_REPLICATION                    1  0.5494735 3.121551e-01
5 PID_MYC_ACTIVPATHWAY                    1  0.6393027 2.170160e-02
6 REACTOME_METABOLISM_OF_NUCLEOTIDES      1  0.5961217 1.064937e-01
  FDR         
1 0.9560054810
2 0.0005816211
3 0.0113659048
4 0.5399506993
5 0.0837394482
6 0.2668264450

In [103]:
ins_lv_filtered <- multiplier_summary %>% 
dplyr::filter(FDR < 0.05 & AUC > 0.7) %>% 
dplyr::left_join(kruskal_test_results) %>% 
dplyr::filter(p_adjusted < 0.05) %>% 
dplyr::arrange(p_adjusted, LV)

dim(ins_lv_filtered)
print(ins_lv_filtered)

Joining with `by = join_by(LV)`


[1] 290   6

                                                                                                           pathway
1                                                                                    KEGG_ECM_RECEPTOR_INTERACTION
2                                                                                      KEGG_PPAR_SIGNALING_PATHWAY
3                                                                                       IRIS_DendriticCell-Control
4                                                                                               SVM Macrophages M2
5                                                                                      SVM Dendritic cells resting
6                                                                                               IRIS_Monocyte-Day0
7                                                                                                       DMAP_MONO2
8                                                                               

In [101]:
sig_lv_data_long <- lv_data_long %>% 
dplyr::filter(LV %in% ins_lv_filtered$LV)

# Calculate mean values for each group and LV
mean_values <- sig_lv_data_long %>%
  group_by(LV, Group) %>%
  summarise(mean_value = mean(Value), .groups = 'drop')

# Plotting options
options(repr.plot.width = 20, repr.plot.height = 80, repr.plot.res = 250)

# Create the plot with only significant LVs and fewer columns
plot <- ggplot(sig_lv_data_long, aes(x = Group, y = Value, fill = Group)) +
  geom_violin(trim = FALSE) +
  stat_summary(fun = mean, geom = "point", color = "black", size = 2) +
  geom_text(data = mean_values, aes(x = Group, y = mean_value, label = round(mean_value, 2)), 
            color = "black", nudge_y = 1) + # Adjust mean values as text
  facet_wrap(~ LV, scales = "free_x", ncol = 3) + # Adjust the number of columns here
  labs(x = NULL, y = "Loading") +
  theme_bw() +
  theme(
    axis.title.x = element_blank(),
    axis.text.x = element_blank(),
    axis.ticks.x = element_blank(),
    legend.title = element_blank()
  ) +
  scale_fill_manual(values = c("BETA" = "#097969", "INS" = "#C70039", "HI" = '#AFE1AF')) +
  stat_compare_means(comparisons = list(c("INS", "BETA"), c("INS", "HI"), c("BETA", "HI")), 
                     method = "wilcox.test", label = "p.signif", hide.ns = TRUE) +
  guides(
    fill = guide_legend(override.aes = list(shape = c(NA, NA, NA), linetype = c(0, 0, 0))),
    color = guide_legend(override.aes = list(shape = c(16), linetype = c(0), color = "black"))
  )

# Display the plot
print(plot)